# 第三次作业：年报格式准则解析

## 导入模块并列出所有准则文件


In [6]:
import os
import re
import fitz # pip install pymupdf
import csv

filenames = os.listdir()
prefix = '公开发行证券的公司信息披露内容与格式准则第2号'

# 须点击上面列表中链接，下载四个修订版本PDF文件，
# 并放置在该代码文件所在文件夹。

# 筛选出格式准则文件
pdf = [f for f in filenames if f.startswith(prefix) and f.endswith('.pdf')]
# 提取修订年份
year = [f[-12:-5] for f in pdf]
#
for f in pdf:
    print(f)
print(year)

公开发行证券的公司信息披露内容与格式准则第2号——年度报告的内容与格式（2012年修订）.pdf
公开发行证券的公司信息披露内容与格式准则第2号——年度报告的内容与格式（2016年修订）.pdf
公开发行证券的公司信息披露内容与格式准则第2号——年度报告的内容与格式（2017年修订）.pdf
公开发行证券的公司信息披露内容与格式准则第2号——年度报告的内容与格式（2021年修订）.pdf
['2012年修订', '2016年修订', '2017年修订', '2021年修订']


## 获取文本

### getText() getSubtext()函数
- 函数 getText()

- 函数getSubtext()

In [ ]:
# 提取PDF文本，因有一份无法被pdfplumber库提取，故采用pymupdf
def getText(pdf):
    text = ''
    doc = fitz.open(pdf)
    for page in doc:
        text += page.getText()
    doc.close()
    return(text)

def getSubtext(pdf):
    text = getText(pdf)
    p1 = re.compile('第二章\s*年度报告正文(.*)第三章\s*年度报告摘要',
                    re.DOTALL)
    subtext = p1.search(text).group(0)
    return(subtext)

### 获取目录函数 getTOC()

In [10]:
# 主要部分
def getTOC(pdf):
    subtext = getSubtext(pdf)
    p = re.compile('(?<=\\n)(第\w{1,2}节)\s+(.*)(?=\\n)')
    listOftuple = p.findall(subtext)
    return(listOftuple)

# text_list = [getText(f) for f in pdf]
toc = [getTOC(f) for f in pdf]
for t in toc:
    for item in t:
        print(item)
    print('\n')

('第一节', '重要提示、目录和释义')
('第二节', '公司简介')
('第三节', '会计数据和财务指标摘要')
('第四节', '董事会报告')
('第五节', '重要事项')
('第六节', '股份变动及股东情况')
('第七节', '董事、监事、高级管理人员和员工情况')
('第八节', '公司治理')
('第九节', '内部控制')
('第十节', '财务报告')


('第一节', '重要提示、目录和释义')
('第二节', '公司简介和主要财务指标')
('第三节', '公司业务概要')
('第四节', '经营情况讨论与分析')
('第五节', '重要事项')
('第六节', '股份变动及股东情况')
('第七节', '优先股相关情况')
('第八节', '董事、监事、高级管理人员和员工情况')
('第九节', '公司治理')
('第十节', '公司债券相关情况')
('第十一节', '财务报告')
('第十二节', '备查文件目录')


('第一节', '重要提示、目录和释义')
('第二节', '公司简介和主要财务指标')
('第三节', '公司业务概要')
('第四节', '经营情况讨论与分析')
('第五节', '重要事项')
('第六节', '股份变动及股东情况')
('第七节', '优先股相关情况')
('第八节', '董事、监事、高级管理人员和员工情况')
('第九节', '公司治理')
('第十节', '公司债券相关情况')
('第十一节', '财务报告')
('第十二节', '备查文件目录')


('第一节', '重要提示、目录和释义')
('第二节', '公司简介和主要财务指标')
('第三节', '管理层讨论与分析')
('第四节', '公司治理')
('第五节', '环境和社会责任')
('第六节', '重要事项')
('第七节', '股份变动及股东情况')
('第八节', '优先股相关情况')
('第九节', '债券相关情况')
('第十节', '财务报告')




### 获取节内容函数 getTOC_content()

In [ ]:
def getTOC_content(pdf):
    subtext = getSubtext(pdf)
    p = re.compile('(?<=\\n)(第\w{1,2}节)\s+(.*)(?=\\n)')
    index = []
    for match in p.finditer(subtext):
        s = match.start()
        e = match.end()
        index.append((s,e))
    #
    content = []
    for i in range(len(index)-1):
        s = index[i][1]
        e = index[i+1][0]
        content.append(subtext[s:e])
    last_start = index[-1][1]
    last_end = subtext.rfind('\n第三章')
    content.append(subtext[last_start:last_end])
    return((index,content))

# index, content = getTOC_content(pdf[0])
list_of_content = [getTOC_content(f) for f in pdf]

### 导出为HTML格式

In [11]:
def export_to_html(pdf,toc,content,year):
    f = open('homework3_output_template.html', encoding='utf-8')
    html = f.read()
    f.close()
    template = '<div><h3>%s</h3><p>%s</p></div>'
    toc_list = [t[0]+' '+ t[1] for t in toc]
    div = [template % (t,c) for (t,c) in zip(toc_list, content)]
    div = ''.join(div)
    html = html % div
    f = open('年报格式准则_%s.html' % year, 'w',encoding='utf-8')
    f.write(html)
    f.close()
    return()

content_list = [c[1] for c in list_of_content]
for i in range(len(pdf)):
    export_to_html(pdf[i], toc[i], content_list[i],year[i])

## 最终结果

- [年报格式准则_2012年修订.html](年报格式准则_2012年修订.html)

- [年报格式准则_2016年修订.html](年报格式准则_2016年修订.html)

- [年报格式准则_2017年修订.html](年报格式准则_2017年修订.html)

- [年报格式准则_2021年修订.html](年报格式准则_2021年修订.html)